# Exploring the scraped data

In [38]:
import numpy as np
import pandas as pd
import re
import sqlite3
import time
from matplotlib import pyplot as plt
from datetime import datetime
import seaborn as sns
import ast
import json
from collections import defaultdict

np.random.seed(173)

In [2]:
db_armenpress = sqlite3.connect("Armenpress/scraping.db")
db_newsam = sqlite3.connect("Newsam/scraping.db")
db_tertam = sqlite3.connect("Tertam/scraping.db")

In [3]:
df_armenpress = pd.read_sql_query("select * from article", db_armenpress)
df_newsam = pd.read_sql_query("select * from article", db_newsam)
df_tertam = pd.read_sql_query("select * from article", db_tertam)

In [4]:
df_tertam.time = pd.to_datetime(df_tertam.time)
df_newsam.time = pd.to_datetime(df_newsam.time)
df_armenpress.time = pd.to_datetime(df_armenpress.time)

In [ ]:
[([df_armenpress, df_newsam, df_tertam])]

In [5]:
df_armenpress

id                                           headline  \
0        218011  AREMNIAN PRESIDENT SERZH SARGSYAN RECEIVES EXE...   
1        218012  ISSUES ON DEVELOPMENT OF AGRICULTURE SPHERE DI...   
2        218013  CREDIT AGREEMENT OF 25 MILLION USD SIGNED WITH...   
3        218014  INTERNATIONAL OBSERVERS REGISTER THAT THE GENE...   
4        218015  MATTHEW BRYZA SAYS OSCE MINSK GROUP CO-CHAIRS ...   
...         ...                                                ...   
144134  1124334  Armenia and Tunisia to lift visa requirements ...   
144135  1124335  Shoghakat Vardanyan’s war documentary ‘1489’ w...   
144136  1124340  Daniel Hilaire: “At Fast Bank, we are continuo...   
144137  1124341  Yerevan police officer injured while respondin...   
144138  1124344  EU ‘demanding very clearly that people of Nago...   

                      time                                            content  \
0      2009-06-08 00:00:00  YEREVAN, JUNE 9, ARMENPRESS:Armenian President...   
1      2009-06-08 00:00:00  YEREVAN, JUNE 9, ARMENPRESS:Director of the Co...   
2      2009-06-04 00:00:00  YEREVAN, JUNE 5, ARMENPRESS:The credit agreeme...   
3      2008-12-30 00:00:00  YEREVAN, JUNE 1, ARMENPRESS:The observing miss...   
4      2009-06-01 00:00:00  BAKU, JUNE 1, ARMENPRESS:OSCE Minsk group is o...   
...                    ...                                                ...   
144134 2023-11-17 11:06:31  YEREVAN, NOVEMBER 17, ARMENPRESS. Armenia and ...   
144135 2023-11-17 11:20:02  YEREVAN, NOVEMBER 17, ARMENPRESS. Armenian fil...   
144136 2023-11-17 11:49:17  YEREVAN, NOVEMBER 17, ARMENPRESS. Digital bank...   
144137 2023-11-17 11:51:28  YEREVAN, NOVEMBER 17, ARMENPRESS. One of the t...   
144138 2023-11-17 12:12:47  BRUSSELS, NOVEMBER 17, ARMENPRESS. The Europea...   

                                                 feedback  
0       {\n  "entities": [\n    {\n      "name": "Serz...  
1       {\n  "entities": [\n    {\n      "name": "Davi...  
2       {"entities": [\n  {"name": "World Bank", "sent...  
3       {\n  "entities": [\n    {"name": "CoE Congress...  
4       {\n  "entities": [\n    {\n      "name": "Matt...  
...                                                   ...  
144134                                               None  
144135                                               None  
144136                                               None  
144137                                               None  
144138                                               None  

[144139 rows x 5 columns]

In [6]:
(sample := df_armenpress[~df_armenpress.feedback.isna()].sample(1000))

id                                           headline  \
70068    867244  French President - Trump’s win opens up a peri...   
90429    937732  Russian gas price is exclusive for Armenia, bu...   
46336    777525   Obama among most aggressive U.S. Presidents: CNN   
135262  1096837  Zakharova refers to Azerbaijani criticism of R...   
32069    705548  Obama’s brother from Kenya is running for gove...   
...         ...                                                ...   
136131  1099408  By blocking the corridor Azerbaijan aims at di...   
137528  1102947  Over 250% output growth, expansion of team, ma...   
125995  1068374  Congressman Schiff calls on US government to d...   
60582    836877                   14 dead in Afghanistan terrorism   
117606  1035461  “The time for reaching a lasting peace is now”...   

                      time                                            content  \
70068  2016-11-09 17:51:01  YEREVAN, NOVEMBER 9, ARMENPRESS. French presid...   
90429  2018-06-15 22:11:13  YEREVAN, JUNE 15, ARMENPRESS. Prime Miniter of...   
46336  2014-09-24 12:45:57  YEREVAN, SEPTEMBER 24, ARMENPRESS. Which U.S. ...   
135262 2022-11-09 19:28:21  YEREVAN, NOVEMBER 9, ARMENPRESS. Russia has a ...   
32069  2013-01-19 16:06:13  YEREVAN, JANUARY 19, ARMENPRESS: U.S. Presiden...   
...                    ...                                                ...   
136131 2022-12-12 16:22:48  YEREVAN, DECEMBER 12, ARMENPRESS. Speaker of P...   
137528 2023-02-01 13:50:49  YEREVAN, FEBRUARY 1, ARMENPRESS.  PROFAL GROUP...   
125995 2021-11-17 10:16:24  WASHINGTON D.C., NOVEMBER 17, ARMENPRESS. Unit...   
60582  2016-02-22 20:35:20  YEREVAN, FEBRUARY 22, ARMENPRESS. 14 people, i...   
117606 2020-11-20 14:09:36  YEREVAN, NOVEMBER 20, ARMENPRESS. The United S...   

                                                 feedback  
70068   {\n  "entities": [\n    {\n      "name": "Fran...  
90429   {\n  "entities": [\n    {\n      "name": "Arme...  
46336   {\n  "entities": [\n    {\n      "name": "Bara...  
135262  {\n  "entities": [\n    {"name": "Russia", "se...  
32069   {\n  "entities": [\n    {"name": "Barack Obama...  
...                                                   ...  
136131  {\n  "entities": [\n    {\n      "name": "Azer...  
137528  {\n  "entities": [\n    {\n      "name": "PROF...  
125995  {\n  "entities": [\n    {\n      "name": "Azer...  
60582   {\n  "entities": [\n    {\n      "name": "Afgh...  
117606  {\n  "entities": [\n    {\n      "name": "Unit...  

[1000 rows x 5 columns]

In [23]:
(dicts := sample.feedback.apply(lambda x: ast.literal_eval(x.replace("\n", ""))))

70068     {'entities': [{'name': 'François Hollande', 's...
90429     {'entities': [{'name': 'Armenia', 'sentiment':...
46336     {'entities': [{'name': 'Barack Obama', 'sentim...
135262    {'entities': [{'name': 'Russia', 'sentiment': ...
32069     {'entities': [{'name': 'Barack Obama', 'sentim...
                                ...                        
136131    {'entities': [{'name': 'Azerbaijan', 'sentimen...
137528    {'entities': [{'name': 'PROFAL GROUP', 'sentim...
125995    {'entities': [{'name': 'Azerbaijan', 'sentimen...
60582     {'entities': [{'name': 'Afghanistan', 'sentime...
117606    {'entities': [{'name': 'United States', 'senti...
Name: feedback, Length: 1000, dtype: object

In [26]:
dicts[~dicts.apply(lambda x: hasattr(x, "keys"))]

66    [{'name': 'Asian Development Bank', 'sentiment...
31    [{'name': 'Sergey Lavrov', 'sentiment': 'posit...
Name: feedback, dtype: object

In [29]:
dicts = df_armenpress[~df_armenpress.feedback.isna()].feedback.apply(lambda x: ast.literal_eval(x.replace("\n", "")))

0         {'entities': [{'name': 'Serzh Sargsyan', 'sent...
1         {'entities': [{'name': 'David Hakhverdyan', 's...
2         {'entities': [{'name': 'World Bank', 'sentimen...
3         {'entities': [{'name': 'CoE Congress of Local ...
4         {'entities': [{'name': 'Matthew Bryza', 'senti...
                                ...                        
144078    {'entities': [{'name': 'Nagorno-Karabakh', 'se...
144104    {'entities': [{'name': 'United States', 'senti...
144115    {'entities': [{'name': 'FLYONE ARMENIA', 'sent...
144116    {'entities': [{'name': 'Azerbaijan', 'sentimen...
144123    {'entities': [{'name': 'Estonia', 'sentiment':...
Name: feedback, Length: 11686, dtype: object

In [32]:
dicts[~dicts.apply(lambda x: hasattr(x, "keys") and "entities" in x.keys())]

35588     {'named_entities': [{'name': 'Millennium Chall...
21446     {'named_entities': [{'name': 'Armenia', 'senti...
59727     {'named_entities': [{'name': 'Russian ruble', ...
66        [{'name': 'Asian Development Bank', 'sentiment...
31        [{'name': 'Sergey Lavrov', 'sentiment': 'posit...
19320     {'namedEntities': [{'name': 'Russian Embassy o...
130393    {'named_entities': ['Nagorno-Karabakh conflict...
Name: feedback, dtype: object

In [36]:
def strpdict(string: str) -> dict:
    try:
        return ast.literal_eval(string)
    except Exception as e:
        print(e)


(dicts := df_newsam[~df_newsam.feedback.isna()].feedback.apply(lambda x: strpdict(x.replace("\n", ""))))

'{' was never closed (<unknown>, line 1)
'{' was never closed (<unknown>, line 1)
'{' was never closed (<unknown>, line 1)
'[' was never closed (<unknown>, line 1)
'{' was never closed (<unknown>, line 1)


17        {'entities': [{'name': 'Russian stabilizing lo...
36        {'entities': [{'name': 'Turkish-Russian issues...
49        {'entities': [{'name': 'Bako Sahakyan', 'senti...
63        {'entities': [{'name': 'Barack Obama', 'sentim...
79        {'entities': [{'name': 'UC Rusal', 'sentiment'...
                                ...                        
219263    {'entities': [{'name': 'Syria', 'sentiment': '...
219295    {'entities': [{'name': 'Mongolia', 'sentiment'...
219359    {'entities': [{'name': 'Alen Simonyan', 'senti...
219363    {'entities': [{'name': 'CSTO', 'sentiment': 'p...
219367    {'entities': [{'name': 'Russia', 'sentiment': ...
Name: feedback, Length: 15807, dtype: object

In [37]:
(dicts := dicts[dicts.apply(lambda x: hasattr(x, "keys") and "entities" in x.keys())])

17        {'entities': [{'name': 'Russian stabilizing lo...
36        {'entities': [{'name': 'Turkish-Russian issues...
49        {'entities': [{'name': 'Bako Sahakyan', 'senti...
63        {'entities': [{'name': 'Barack Obama', 'sentim...
79        {'entities': [{'name': 'UC Rusal', 'sentiment'...
                                ...                        
219263    {'entities': [{'name': 'Syria', 'sentiment': '...
219295    {'entities': [{'name': 'Mongolia', 'sentiment'...
219359    {'entities': [{'name': 'Alen Simonyan', 'senti...
219363    {'entities': [{'name': 'CSTO', 'sentiment': 'p...
219367    {'entities': [{'name': 'Russia', 'sentiment': ...
Name: feedback, Length: 15707, dtype: object

In [51]:
# defining a preset for accounting connections by sentiment
entities = defaultdict(lambda: {
    "positive": 0,
    "negative": 0,
    "neutral": 0,
    "connections": [
        defaultdict(lambda: 0),
        defaultdict(lambda: 0),
        defaultdict(lambda: 0)
    ]  # positionally correspondive
})

possible_sentiments = ["positive", "negative", "neutral"]

def account_response(resp: dict):
    # preprocess name and sentiment
    entity_sentiments = {
        ent["name"].strip().lower(): other_sent
        for ent
        in resp["entities"]
        if (other_sent := ent["sentiment"].strip().lower()) in possible_sentiments
    }

    for name, sentiment in entity_sentiments.items():
        # account sentiment
        entities[name][sentiment] += 1

        # account connections by sentiment
        for other_name, other_sentiment in [(n, s) for n, s in entity_sentiments.items() if n != name]:
            entities[name]["connections"][possible_sentiments.index(other_sentiment)][other_name] += 1

dicts.apply(account_response)
entities

defaultdict(<function __main__.<lambda>()>,
            {'russian stabilizing loan': {'positive': 0,
              'negative': 0,
              'neutral': 1,
              'connections': [defaultdict(<function __main__.<lambda>.<locals>.<lambda>()>,
                           {}),
               defaultdict(<function __main__.<lambda>.<locals>.<lambda>()>,
                           {'imf': 1, 'wb (world bank)': 1}),
               defaultdict(<function __main__.<lambda>.<locals>.<lambda>()>,
                           {'armenian industrial enterprises': 1})]},
             'armenian industrial enterprises': {'positive': 0,
              'negative': 0,
              'neutral': 1,
              'connections': [defaultdict(<function __main__.<lambda>.<locals>.<lambda>()>,
                           {}),
               defaultdict(<function __main__.<lambda>.<locals>.<lambda>()>,
                           {'imf': 1, 'wb (world bank)': 1}),
               defaultdict(<function __main__.<l

In [59]:
len([name for name, stats in entities.items() if (
    (stats["positive"] if type(stats["positive"]) is int else 0) + 
    (stats["negative"] if type(stats["negative"]) is int else 0) +
    (stats["neutral"] if type(stats["neutral"]) is int else 0)) > 10])

648

In [60]:
len(entities)

21611

In [48]:
other_types_of_sentiments = set()
not_in_3_sentiment = dicts[~dicts.apply(lambda x: all([(ent["sentiment"].lower() in ["positive", "negative", "neutral"]) for ent in x["entities"]]))]
not_in_3_sentiment.apply(lambda x: [other_types_of_sentiments.add(ent["sentiment"]) for ent in x["entities"]])
other_types_of_sentiments

874        [None, None, None, None, None, None, None, None]
2056                               [None, None, None, None]
2646                   [None, None, None, None, None, None]
2719             [None, None, None, None, None, None, None]
4317      [None, None, None, None, None, None, None, Non...
                                ...                        
207238    [None, None, None, None, None, None, None, Non...
207934                 [None, None, None, None, None, None]
210296    [None, None, None, None, None, None, None, Non...
216897     [None, None, None, None, None, None, None, None]
218192                       [None, None, None, None, None]
Name: feedback, Length: 98, dtype: object

In [49]:
other_types_of_sentiments

{'Mixed',
 'Negative',
 'Neutral',
 'Positive',
 'concerned',
 'contested',
 'controversial',
 'mixed',
 'n/a',
 'negaitive',
 'negative',
 'neutral',
 'positive',
 'potentially negative',
 'uncertain',
 'worrismome'}

In [44]:
dicts

17        {'entities': [{'name': 'Russian stabilizing lo...
36        {'entities': [{'name': 'Turkish-Russian issues...
49        {'entities': [{'name': 'Bako Sahakyan', 'senti...
63        {'entities': [{'name': 'Barack Obama', 'sentim...
79        {'entities': [{'name': 'UC Rusal', 'sentiment'...
                                ...                        
219263    {'entities': [{'name': 'Syria', 'sentiment': '...
219295    {'entities': [{'name': 'Mongolia', 'sentiment'...
219359    {'entities': [{'name': 'Alen Simonyan', 'senti...
219363    {'entities': [{'name': 'CSTO', 'sentiment': 'p...
219367    {'entities': [{'name': 'Russia', 'sentiment': ...
Name: feedback, Length: 15707, dtype: object

In [50]:
dicts

17        {'entities': [{'name': 'Russian stabilizing lo...
36        {'entities': [{'name': 'Turkish-Russian issues...
49        {'entities': [{'name': 'Bako Sahakyan', 'senti...
63        {'entities': [{'name': 'Barack Obama', 'sentim...
79        {'entities': [{'name': 'UC Rusal', 'sentiment'...
                                ...                        
219263    {'entities': [{'name': 'Syria', 'sentiment': '...
219295    {'entities': [{'name': 'Mongolia', 'sentiment'...
219359    {'entities': [{'name': 'Alen Simonyan', 'senti...
219363    {'entities': [{'name': 'CSTO', 'sentiment': 'p...
219367    {'entities': [{'name': 'Russia', 'sentiment': ...
Name: feedback, Length: 15707, dtype: object